In [ ]:
from urlparse import urljoin
import requests
from bs4 import BeautifulSoup
import time

base_url = 'http://www.pulitzer.org/archives/'
title_list = []
winnerlist = []

for i in range(5085,7197):
    print i
    winner_dict["link"] = next_page
    
    winner_dict = {}
    
    next_page = 'http://www.pulitzer.org/archives/'+ str(i)
    #print next_page

    page = BeautifulSoup(requests.get(next_page).content)
    
    title = page.find("h2",attrs = {"class": "archives-title"})
    if title:
        winner_dict["title"] = title.string
    
    authordiv = page.find("div","field field-type-text field-field-authors")
    
    if authordiv:
        authorname = authordiv.find("div","field-item")
        clean_author = authorname.getText().lower().replace("  "," ").replace("by:","").replace("staff writer","").strip()
        winner_dict["authors"] = clean_author
    
    
    pubdate = page.find("div","field field-type-text field-field-date")
    if pubdate:
        pubdate = pubdate.getText().strip()
        winner_dict["pubdate"] = pubdate
    
    win_datediv = page.find("h2", "archives_year_award")
    if win_datediv:
        win_date =  win_datediv.find("span", "archives_year").getText()
        winner_dict['win_date'] = win_date
    
        award = win_datediv.find("span", "archives_award")
        if award:
            award = award.getText()
            winner_dict['award'] = award
    
    story_td = page.find("td")
    
    if story_td:
        paragraphs = story_td.find_all("p")
        texts = ""
        for p in paragraphs:
            if p and not p.has_attr('align'):
                texts = texts + p.getText()
        winner_dict["text"] = texts
        winnerlist.append(winner_dict)
        print winner_dict
        
        
    time.sleep(1)
    
    

5085
5086
5087
5088
5089
5090
5091
5092
5093
5094
5095
5096
5097
5098
5099
5100
5101
5102
5103
5104
5105
5106
5107
5108
5109
5110
5111
5112
5113
5114
5115
5116
5117
5118
5119
5120
5121
5122
5123
5124
5125
5126
5127
5128
5129
5130
5131
5132
5133
5134
5135
5136
5137
5138
{'text': '', 'authors': u'stephen breen', 'win_date': u'1998', 'award': u'Editorial Cartooning', 'title': u'Editorial Cartooning: Archived Images'}
5139
{'text': '', 'authors': u'stephen breen', 'win_date': u'1998', 'award': u'Editorial Cartooning', 'title': u'Editorial Cartooning: Archived Images'}
5140
{'text': '', 'authors': u'stephen breen', 'win_date': u'1998', 'award': u'Editorial Cartooning', 'title': u'Editorial Cartooning: Archived Images'}
5141
{'text': '', 'authors': u'stephen breen', 'win_date': u'1998', 'award': u'Editorial Cartooning', 'title': u'Editorial Cartooning: Archived Images'}
5142
{'text': '', 'authors': u'stephen breen', 'win_date': u'1998', 'award': u'Editorial Cartooning', 'title': u'Editorial 

In [51]:
corpus = "".join([item["text"] for item in winnerlist if len(item["text"])>1000])


In [ ]:
"""
Minimal character-level Vanilla RNN model. Written by Andrej Karpathy (@karpathy)
BSD License
"""
import numpy as np

# data I/O
#data = open('input.txt', 'r').read() # should be simple plain text file
data = corpus
chars = list(set(data))
data_size, vocab_size = len(data), len(chars)
print 'data has %d characters, %d unique.' % (data_size, vocab_size)
char_to_ix = { ch:i for i,ch in enumerate(chars) }
ix_to_char = { i:ch for i,ch in enumerate(chars) }

# hyperparameters WHATTTT??!?!
hidden_size = 100 # size of hidden layer of neurons
seq_length = 25 # number of steps to unroll the RNN for
learning_rate = 1e-1

# model parameters
Wxh = np.random.randn(hidden_size, vocab_size)*0.01 # input to hidden
Whh = np.random.randn(hidden_size, hidden_size)*0.01 # hidden to hidden
Why = np.random.randn(vocab_size, hidden_size)*0.01 # hidden to output
bh = np.zeros((hidden_size, 1)) # hidden bias
by = np.zeros((vocab_size, 1)) # output bias

def lossFun(inputs, targets, hprev):
  """
  inputs,targets are both list of integers.
  hprev is Hx1 array of initial hidden state
  returns the loss, gradients on model parameters, and last hidden state
  """
  xs, hs, ys, ps = {}, {}, {}, {}
  hs[-1] = np.copy(hprev)
  loss = 0
  # forward pass
  for t in xrange(len(inputs)):
    xs[t] = np.zeros((vocab_size,1)) # encode in 1-of-k representation
    xs[t][inputs[t]] = 1
    hs[t] = np.tanh(np.dot(Wxh, xs[t]) + np.dot(Whh, hs[t-1]) + bh) # hidden state
    ys[t] = np.dot(Why, hs[t]) + by # unnormalized log probabilities for next chars
    ps[t] = np.exp(ys[t]) / np.sum(np.exp(ys[t])) # probabilities for next chars
    loss += -np.log(ps[t][targets[t],0]) # softmax (cross-entropy loss)
  # backward pass: compute gradients going backwards
  dWxh, dWhh, dWhy = np.zeros_like(Wxh), np.zeros_like(Whh), np.zeros_like(Why)
  dbh, dby = np.zeros_like(bh), np.zeros_like(by)
  dhnext = np.zeros_like(hs[0])
  for t in reversed(xrange(len(inputs))):
    dy = np.copy(ps[t])
    dy[targets[t]] -= 1 # backprop into y
    dWhy += np.dot(dy, hs[t].T)
    dby += dy
    dh = np.dot(Why.T, dy) + dhnext # backprop into h
    dhraw = (1 - hs[t] * hs[t]) * dh # backprop through tanh nonlinearity
    dbh += dhraw
    dWxh += np.dot(dhraw, xs[t].T)
    dWhh += np.dot(dhraw, hs[t-1].T)
    dhnext = np.dot(Whh.T, dhraw)
  for dparam in [dWxh, dWhh, dWhy, dbh, dby]:
    np.clip(dparam, -5, 5, out=dparam) # clip to mitigate exploding gradients
  return loss, dWxh, dWhh, dWhy, dbh, dby, hs[len(inputs)-1]

def sample(h, seed_ix, n):
  """ 
  sample a sequence of integers from the model 
  h is memory state, seed_ix is seed letter for first time step
  """
  x = np.zeros((vocab_size, 1))
  x[seed_ix] = 1
  ixes = []
  for t in xrange(n):
    h = np.tanh(np.dot(Wxh, x) + np.dot(Whh, h) + bh)
    y = np.dot(Why, h) + by
    p = np.exp(y) / np.sum(np.exp(y))
    ix = np.random.choice(range(vocab_size), p=p.ravel())
    x = np.zeros((vocab_size, 1))
    x[ix] = 1
    ixes.append(ix)
  return ixes

n, p = 0, 0
mWxh, mWhh, mWhy = np.zeros_like(Wxh), np.zeros_like(Whh), np.zeros_like(Why)
mbh, mby = np.zeros_like(bh), np.zeros_like(by) # memory variables for Adagrad
smooth_loss = -np.log(1.0/vocab_size)*seq_length # loss at iteration 0
while True:
  # prepare inputs (we're sweeping from left to right in steps seq_length long)
  if p+seq_length+1 >= len(data) or n == 0: 
    hprev = np.zeros((hidden_size,1)) # reset RNN memory
    p = 0 # go from start of data
  inputs = [char_to_ix[ch] for ch in data[p:p+seq_length]]
  targets = [char_to_ix[ch] for ch in data[p+1:p+seq_length+1]]

  # sample from the model now and then
  if n % 100 == 0:
    sample_ix = sample(hprev, inputs[0], 200)
    txt = ''.join(ix_to_char[ix] for ix in sample_ix)
    print '----\n %s \n----' % (txt, )

  # forward seq_length characters through the net and fetch gradient
  loss, dWxh, dWhh, dWhy, dbh, dby, hprev = lossFun(inputs, targets, hprev)
  smooth_loss = smooth_loss * 0.999 + loss * 0.001
  if n % 100 == 0: print 'iter %d, loss: %f' % (n, smooth_loss) # print progress
  
  # perform parameter update with Adagrad
  for param, dparam, mem in zip([Wxh, Whh, Why, bh, by], 
                                [dWxh, dWhh, dWhy, dbh, dby], 
                                [mWxh, mWhh, mWhy, mbh, mby]):
    mem += dparam * dparam
    param += -learning_rate * dparam / np.sqrt(mem + 1e-8) # adagrad update

  p += seq_length # move data pointer
  n += 1 # iteration counter 


data has 14831379 characters, 125 unique.
----
 öö] _55
h—"C+hTQómMGY·nèiqk:½jk-MãQô}Yr#8>]1J#Hi£;PáS\O\rpí4ï{ñH,î-çjCLóô*/fm)ü*;%zG—MVK	ÔR*·—½è–KvËü'O(>éb7RxK—twKfc­óURJ4èB]$%·aËKx]E%è+|`tñK·0bNñ=|@c In*i—%-—%@,"L17nk(("Kï¤DC*8
d
ósË 4PK@68 
----
iter 0, loss: 120.707841
----
 at
 c,trersseria,r c Rst, acnheetoheoamtfife cfn x 
 rxaR
ir,rte
yeetaaetan Idida,iarixr yor,heR y,txcch
 
atnaa
a a troratewnaaay s,ya rat ,a ,a
d,aaehrt ,taxiraed,tanis
eaaSiw.d ,koerelaaka
oaer,pda 
----
iter 100, loss: 119.227631
----
  owo  inkttociai ho ah  naert oshcee oiodnhfu h eev ohnrsmieke
oeoibs aaao omdoi bh eihIs m o eahsr  P  eia'Seee  edhseeoectuo cdeeo hoe hoe  otm    memoshe dhhei ta  hnoortthwt  nu  h.oh .ho o oer es 
----
iter 200, loss: 115.872378
----
 emrdsskgrnaabb itBr edgafhecuessrcndfnorf otorsurdpob
s euur 
u l un
irne dsooarnrd riHkdrnnrunrsetour k itonou,rra rr auu itad nenuoe uan
   nartoniuniaru  ru ucofhguud a marenuno arfewrurrsp rryr,se 
----
iter 300, loss: 112.849862
